In [31]:
import pandas as pd
import requests 
from xml.etree import ElementTree



In [19]:
environments = ["local", "google_colab"]
# please select one of the environments
selected_env = environments[0]
chunk_size = 30 ** 6
TrafficEvents = None
WeatherEvents = None

OSRM_BASIC_URL = "https://etastg.bluebitsoft.com/"
OSM_BASIC_URL = "https://api.openstreetmap.org/api/0.6/"
if selected_env == "local":
    TrafficEvents = {
        "name": "TrafficEvents",
        "file_name": "TrafficEvents_Aug16_Dec19_Publish_Road_Construction.csv",
        "path": "/home/amin/CETI/RoadConstruction/TrafficEventData/",
    }
    WeatherEvents = {
        "name": "WeatherEvent",
        "file_name": "WeatherEvents_Aug16_Dec19_Publish.csv",
        "path": "/home/amin/CETI/RoadConstruction/WeatherEventData/",
    }

else:
    TrafficEvents = {
        "name": "TrafficEvents",
        "file_name": "TrafficEvents_Aug16_Dec19_Publish.csv",
        "id": "1uGLJS4uIbiUf7PjVGtQxo2afjClQT8JY",
    }
    WeatherEvents = {
        "name": "WeatherEvent",
        "file_name": "WeatherEvents_Aug16_Dec19_Publish.csv",
        "id": "1iNUrJYyxBxmklh0e6Iy61eXL34UJo6X8",
    }

In [21]:
if selected_env == "google_colab":
    !pip install -U -q PyDrive
    !pip install --upgrade -q gspread

In [22]:
if selected_env == "google_colab":
    from pydrive.auth import GoogleAuth
    from pydrive.drive import GoogleDrive
    from google.colab import auth
    from oauth2client.client import GoogleCredentials

    auth.authenticate_user()
    gauth = GoogleAuth()
    gauth.credentials = GoogleCredentials.get_application_default()
    drive = GoogleDrive(gauth)

    traffic_events_downloaded = drive.CreateFile(TrafficEvents)
    traffic_events_downloaded.GetContentFile(TrafficEvents["file_name"])

    weather_events_downloaded = drive.CreateFile(WeatherEvents)
    weather_events_downloaded.GetContentFile(WeatherEvents["file_name"])

In [23]:

def read_big_data_by_filter_with_key_values(path, filters):
    data = None
    print("method {} is started ".format("read_big_data_filter_with_key_values"))
    print("read csv data is started with file {}".format(path))
    print("chunk size is {}".format(chunk_size))
    for key, value in zip(filters['keys'], filters['values']):
        print("the key is {} and the value is {}".format(filters['keys'], filters['values']))
    for num, df in enumerate(pd.read_csv(path, chunksize=chunk_size), start=1):
        print("continue reading file page num is {}".format(num))
        for key, value in zip(filters['keys'], filters['values']):
            df = df[df[key] == value]
        data = df.append(data)
    print("method {} finished ".format("read_big_data_filter_with_key_values"))
    return data

In [24]:
weather_file_path = WeatherEvents["path"] + WeatherEvents["file_name"]
traffic_file_path = TrafficEvents["path"] + TrafficEvents["file_name"]

if selected_env == "google_colab":
    traffic_file_path = TrafficEvents["file_name"]
    weather_file_path = WeatherEvents["file_name"]
traffic_filters = {
    "keys": ["Type"],
    "values": ["Construction"],
    }
weather_filters = {
    "keys": [],
    "values": [],
}

traffic_events_data = read_big_data_by_filter_with_key_values(traffic_file_path, traffic_filters)
weather_events_data = read_big_data_by_filter_with_key_values(weather_file_path, weather_filters)


method read_big_data_filter_with_key_values is started 
read csv data is started with file /home/amin/CETI/RoadConstruction/TrafficEventData/TrafficEvents_Aug16_Dec19_Publish_Road_Construction.csv
chunk size is 1000000
the key is ['Type'] and the value is ['Construction']
continue reading file page num is 1
method read_big_data_filter_with_key_values finished 
method read_big_data_filter_with_key_values is started 
read csv data is started with file /home/amin/CETI/RoadConstruction/WeatherEventData/WeatherEvents_Aug16_Dec19_Publish.csv
chunk size is 1000000
continue reading file page num is 1
continue reading file page num is 2
continue reading file page num is 3
continue reading file page num is 4
continue reading file page num is 5
method read_big_data_filter_with_key_values finished 


In [8]:
# write to file

# traffic_events_data.to_csv (r'/home/amin/CETI/RoadConstruction/TrafficEventData/export_dataframe.csv', index = False, header=True)

In [34]:
def get_node_details_by_node_id(node_id):
    URL = OSM_BASIC_URL + "node/{}".format(node_id)
    response = requests.get(url = URL)
    result_tree = ElementTree.fromstring(response.content)
    return result_tree

In [44]:
# a = get_node_details_by_node_id(1989098258)

In [45]:
def get_all_ways_contain_node_by_node_id(node_id):
    URL = OSM_BASIC_URL + "node/{}/ways".format(node_id)
    response = requests.get(url = URL)
    result_tree = ElementTree.fromstring(response.content)
    return result_tree

In [46]:
# a = get_all_ways_contain_node_by_node_id(1989098258)

In [42]:
def get_all_nearest_nodes_of_a_location(location, number=1):
    params = {
        "number": number
    }
    URL = OSRM_BASIC_URL + "nearest/v1/driving/{},{}".format(location["longitude"], location["latitude"])
    response = requests.get(url = URL, params = params)
    print(response.json())
    return response.json() 

In [47]:
# a = get_all_nearest_nodes_of_a_location(location = {"latitude": 52.348253, "longitude": 4.890968}, number=6)

In [48]:
for index, data in traffic_events_data.iterrows():
    print(data)
    location = {
        "latitude": data["LocationLat"],
        "longitude": data["LocationLng"]
    }
    print("lat is {} and long is {}".format(data['LocationLat'], data["LocationLng"]))

EventId                                                  T-25594721
Type                                                   Construction
Severity                                                        NaN
TMC                                                             500
Description       Right lane closed due to accident on I-10 East...
StartTime(UTC)                                  2017-08-25 15:33:08
EndTime(UTC)                                    2017-08-25 16:01:48
TimeZone                                                 US/Central
LocationLat                                                 29.8283
LocationLng                                                -94.3905
Distance(mi)                                                   8.89
AirportCode                                                    KBMT
Number                                                          NaN
Street                                                       I-10 E
Side                                            

Name: 212, dtype: object
lat is 30.266748 and long is -97.741821
EventId                                                  T-25613281
Type                                                   Construction
Severity                                                        NaN
TMC                                                             401
Description       Road closed due to Austin Pride Parade 2017 on...
StartTime(UTC)                                  2017-08-27 01:00:00
EndTime(UTC)                                    2017-08-27 05:00:00
TimeZone                                                 US/Central
LocationLat                                                 30.2684
LocationLng                                                -97.7441
Distance(mi)                                                   0.27
AirportCode                                                    KATT
Number                                                          200
Street                                             

Name: 396, dtype: object
lat is 47.609287 and long is -122.338921
EventId                                                  T-25615413
Type                                                   Construction
Severity                                                        NaN
TMC                                                             401
Description       Road closed due to utility work on Stewart St ...
StartTime(UTC)                                  2017-08-26 12:00:00
EndTime(UTC)                                    2017-08-27 02:00:00
TimeZone                                                 US/Pacific
LocationLat                                                 47.6116
LocationLng                                                 -122.34
Distance(mi)                                                   0.13
AirportCode                                                    KBFI
Number                                                          264
Street                                            

Name: 561, dtype: object
lat is 40.709877 and long is -74.160583
EventId                                                  T-25629140
Type                                                   Construction
Severity                                                        NaN
TMC                                                             500
Description       Right lane closed due to construction work on ...
StartTime(UTC)                                  2017-08-28 09:46:30
EndTime(UTC)                                    2017-08-28 17:00:00
TimeZone                                                 US/Eastern
LocationLat                                                 40.8818
LocationLng                                                 -74.592
Distance(mi)                                                  44.06
AirportCode                                                    KMMU
Number                                                          NaN
Street                                             

Name: 719, dtype: object
lat is 39.536564 and long is -104.868355
EventId                                                  T-25644707
Type                                                   Construction
Severity                                                        NaN
TMC                                                             401
Description       Road closed due to construction during the nig...
StartTime(UTC)                                  2017-08-28 03:00:00
EndTime(UTC)                                    2017-08-28 11:01:00
TimeZone                                                US/Mountain
LocationLat                                                 38.8151
LocationLng                                                -104.822
Distance(mi)                                                   3.32
AirportCode                                                    KCOS
Number                                                          NaN
Street                                            

...

Name: 3046, dtype: object
lat is 42.906898 and long is -74.56234
EventId                                                  T-24746157
Type                                                   Construction
Severity                                                        NaN
TMC                                                             701
Description       Left hand shoulder closed due to construction ...
StartTime(UTC)                                  2017-09-26 11:00:00
EndTime(UTC)                                    2017-09-26 21:00:00
TimeZone                                                 US/Eastern
LocationLat                                                 42.9448
LocationLng                                                -74.3597
Distance(mi)                                                  19.17
AirportCode                                                    KSCH
Number                                                          NaN
Street                                             

Name: 3190, dtype: object
lat is 39.80258900000001 and long is -75.055138
EventId                                                  T-24748497
Type                                                   Construction
Severity                                                        NaN
TMC                                                             701
Description       Intermittent lane closures due to construction...
StartTime(UTC)                                  2017-09-26 16:00:00
EndTime(UTC)                                    2017-09-26 18:00:00
TimeZone                                                 US/Eastern
LocationLat                                                  40.928
LocationLng                                                -73.8402
Distance(mi)                                                   1.29
AirportCode                                                    KLGA
Number                                                          NaN
Street                                    

Name: 3325, dtype: object
lat is 32.357487 and long is -96.85479
EventId                                                  T-24768265
Type                                                   Construction
Severity                                                        NaN
TMC                                                             817
Description       Left lane closed due to construction during th...
StartTime(UTC)                                  2017-09-27 01:00:00
EndTime(UTC)                                    2017-09-27 11:00:00
TimeZone                                                 US/Central
LocationLat                                                 32.4746
LocationLng                                                -96.8362
Distance(mi)                                                   11.9
AirportCode                                                    KJWY
Number                                                          NaN
Street                                             

Name: 3469, dtype: object
lat is 43.297569 and long is -73.678947
EventId                                                  T-24782876
Type                                                   Construction
Severity                                                        NaN
TMC                                                             500
Description       Right lane closed due to bridge maintenance wo...
StartTime(UTC)                                  2017-09-27 13:00:00
EndTime(UTC)                                    2017-09-27 19:00:00
TimeZone                                                 US/Eastern
LocationLat                                                  42.548
LocationLng                                                -73.6712
Distance(mi)                                                      0
AirportCode                                                    KALB
Number                                                         1972
Street                                            

KeyboardInterrupt: 